In [ ]:
!pip install -U -q transformers datasets accelerate sentencepiece
from huggingface_hub import notebook_login
notebook_login()

In [ ]:
from datasets import load_dataset

# If the dataset is gated/private, make sure you have run huggingface-cli login
input_dataset = load_dataset("sablo/SHP-2-dpo")
input_dataset

In [ ]:
import re
from itertools import chain

def count_words(text):
    words = re.findall(r"\b\w+\b", text)
    return len(words)

In [5]:
!pip install tiktoken -q
import os

import tiktoken

# To get the tokeniser corresponding to a specific model in the OpenAI API:
enc = tiktoken.encoding_for_model("gpt-4")


def count_tokens(text:str):
    if len(str(text).strip()) < 2:
        return 0

    return len(
            enc.encode(text, allowed_special={"<|endoftext|>"})
        )
count_tokens('ayyyy lmao!')

6

In [6]:
def check_within_ctx(example, max_ctx: int = 4096):

    try:
        words_full_chosen = count_tokens(example["prompt"]) + count_tokens(
            example["chosen"]
        )
        words_full_rejected = count_tokens(example["prompt"]) + count_tokens(
            example["rejected"]
        )
    except Exception as e:
        print(e)
        return False

    return words_full_chosen <= max_ctx and words_full_rejected <= max_ctx


check_within_ctx(input_dataset["train"][0])

True

In [7]:
input_dataset = input_dataset.filter(check_within_ctx, num_proc=16)
input_dataset

Filter (num_proc=16):   0%|          | 0/3491368 [00:00<?, ? examples/s]

Filter (num_proc=16):   0%|          | 0/238852 [00:00<?, ? examples/s]

Filter (num_proc=16):   0%|          | 0/241274 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['post_id', 'domain', 'upvote_ratio', 'seconds_difference', 'score_ratio', 'prompt', 'chosen', 'rejected', 'score_chosen', 'score_rejected'],
        num_rows: 3490705
    })
    validation: Dataset({
        features: ['post_id', 'domain', 'upvote_ratio', 'seconds_difference', 'score_ratio', 'prompt', 'chosen', 'rejected', 'score_chosen', 'score_rejected'],
        num_rows: 238624
    })
    test: Dataset({
        features: ['post_id', 'domain', 'upvote_ratio', 'seconds_difference', 'score_ratio', 'prompt', 'chosen', 'rejected', 'score_chosen', 'score_rejected'],
        num_rows: 241159
    })
})

In [9]:
from datasets import load_dataset, DatasetDict
import os
from collections import Counter
import json
from datasets.utils.logging import disable_progress_bar, enable_progress_bar
from tqdm.auto import tqdm


def get_workers(safety:int= 4):
    return max(1, os.cpu_count()-safety)

total_rows_small = {"train": 90000, "validation": 5000, "test": 5000}



# Function to sample data for a given split
def sample_split_data(split, total_rows):
    # Count domain occurrences
    domain_counts = Counter(input_dataset[split]["domain"])

    # Calculate the total number of rows in the current split
    total_rows_current_split = len(input_dataset[split])
    disable_progress_bar()
    # Calculate the number of rows to sample for each domain
    sample_counts = {
        domain: int((count / total_rows_current_split) * total_rows)
        for domain, count in domain_counts.items()
    }

    # Sample data
    sampled_data = []
    for domain, sample_count in tqdm(sample_counts.items()):
        domain_data = input_dataset[split].filter(
            lambda example: example["domain"] == domain,
            num_proc=get_workers()
        )
        sampled_indices = domain_data.shuffle(seed=42).select(
            range(min(sample_count, len(domain_data)))
        )
        sampled_data.extend(sampled_indices)

    enable_progress_bar()
    return sampled_data


# Sample data for each split
sampled_train = sample_split_data("train", total_rows_small["train"])
sampled_validation = sample_split_data("validation", total_rows_small["validation"])
sampled_test = sample_split_data("test", total_rows_small["test"])

# Combine the samples to create smaller datasets
small_dataset = DatasetDict(
    {
        "train": sampled_train,
        "validation": sampled_validation,
        "test": sampled_test,
    }
)

small_dataset


  0%|          | 0/69 [00:00<?, ?it/s]

  0%|          | 0/124 [00:00<?, ?it/s]

  0%|          | 0/124 [00:00<?, ?it/s]

In [14]:
import pandas as pd
import gc

gc.collect()

from datasets import Dataset
_test = Dataset.from_pandas(pd.DataFrame(sampled_train))
_test

Dataset({
    features: ['post_id', 'domain', 'upvote_ratio', 'seconds_difference', 'score_ratio', 'prompt', 'chosen', 'rejected', 'score_chosen', 'score_rejected'],
    num_rows: 89971
})

In [15]:
# Combine the samples to create smaller datasets
small_dataset = DatasetDict(
    {
        "train": Dataset.from_pandas(pd.DataFrame(sampled_train)),
        "validation": Dataset.from_pandas(pd.DataFrame(sampled_validation)),
        "test": Dataset.from_pandas(pd.DataFrame(sampled_test)),
    }
)

small_dataset

DatasetDict({
    train: Dataset({
        features: ['post_id', 'domain', 'upvote_ratio', 'seconds_difference', 'score_ratio', 'prompt', 'chosen', 'rejected', 'score_chosen', 'score_rejected'],
        num_rows: 89971
    })
    validation: Dataset({
        features: ['post_id', 'domain', 'upvote_ratio', 'seconds_difference', 'score_ratio', 'prompt', 'chosen', 'rejected', 'score_chosen', 'score_rejected'],
        num_rows: 4936
    })
    test: Dataset({
        features: ['post_id', 'domain', 'upvote_ratio', 'seconds_difference', 'score_ratio', 'prompt', 'chosen', 'rejected', 'score_chosen', 'score_rejected'],
        num_rows: 4938
    })
})

In [16]:
small_dataset.push_to_hub('sablo/SHP-2-dpo',
                          config_name='sampled-100k',
                          private=True,
                          commit_message='stratified sampled ds prop. to domain freq'
                          )

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/90 [00:00<?, ?ba/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/5 [00:00<?, ?ba/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/5 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/4.08k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/datasets/sablo/SHP-2-dpo/commit/6cd324ab8b1f832033c30a996c631cc4d31e27f0', commit_message='stratified sampled ds prop. to domain freq', commit_description='', oid='6cd324ab8b1f832033c30a996c631cc4d31e27f0', pr_url=None, pr_revision=None, pr_num=None)